# Karaoke klassificatie 2025

Team Diep Leren en Opereren

Groepsleden:
- Casper Priem - (casperpriem)
- Lars Timmer - (laltir)
- Matthias de Vreede - (matthiasdevreede)
- Willem van Dijk - (willemvandijk)

Voor groepsleden (DELETE AFTER)

- Spreektaal nederlands, dus comments en markdown in het nederlands mieteren
- Heading 2 per onderwerp, daarbinnen heading 3 per vraag
- In dezelfde cel de beschijving van de opdracht gooien

Op het eind doen we nummering


Andere groepen gaven aan dat alleen audio clip of alleen songtexten niet veel deed, dus daar niet heel erg op score letten. Ik verwacht dat de transformer / model naar keuze het beste zal werken.

### Inladen Libraries

In [24]:
# !pip install librosa

In [21]:
import pandas as pd
import os
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import tensorflow as tf
import datetime as dt
import pathlib
import warnings


# Voor audiobestanden
import glob
import librosa
import IPython.display as ipd

warnings.filterwarnings("ignore", category=UserWarning)

## Exploratieve Data Analyse

In [18]:
df_train = pd.read_csv("train.csv")

df_train

filename                                             lyrics  genre
0    blues.00001.wav  I’m in the Mood Lyrics[Verse 1]\nI'm in the mo...  blues
1    blues.00002.wav  (John Lee Hooker)\nThink twice before you go, ...  blues
2    blues.00003.wav  [Intro, Spoken]\n...A little thing I'm going t...  blues
3    blues.00005.wav  Sugar mama, sugar mama, sugar mama please come...  blues
4    blues.00006.wav  My baby left me this morning\nPeople just arou...  blues
..               ...                                                ...    ...
532   rock.00094.wav  [Chorus]\nDon’t stop\nIsn’t it funny how you s...   rock
533   rock.00096.wav  [Verse 1]\nHer hair, soft drifted snow\nDeath ...   rock
534   rock.00097.wav  [Verse 1]\nYour knuckles whiten on the wheel\n...   rock
535   rock.00098.wav  [Verse 1]\nYou know it\nYou show it\nAnd the t...   rock
536   rock.00099.wav  [Verse 1]\nA girl consumed by fire\nWe all kno...   rock

[537 rows x 3 columns]

### Inlezen Audiotracks

Lees de audiotracks in en speel een paar fragmenten uit verschillende genres.

In [22]:
audio_dir = "Test"

audio_files = glob.glob(os.path.join(audio_dir, '*.wav'))  # pas de extensie zo nodig aan

for af in audio_files[:3]:  # eerste 3 bestanden als voorbeeld
    y, sr = librosa.load(af, sr=None)
    duration = len(y) / sr
    print(f"Bestand: {os.path.basename(af)} | SR: {sr} | Duur: {duration:.2f}s")
    display(ipd.Audio(y, rate=sr))

print(audio_files)

Bestand: test.00000.wav | SR: 22050 | Duur: 30.01s


Bestand: test.00001.wav | SR: 22050 | Duur: 30.01s


Bestand: test.00002.wav | SR: 22050 | Duur: 30.00s


['Test\\test.00000.wav', 'Test\\test.00001.wav', 'Test\\test.00002.wav', 'Test\\test.00003.wav', 'Test\\test.00004.wav', 'Test\\test.00005.wav', 'Test\\test.00006.wav', 'Test\\test.00007.wav', 'Test\\test.00008.wav', 'Test\\test.00009.wav', 'Test\\test.00010.wav', 'Test\\test.00011.wav', 'Test\\test.00012.wav', 'Test\\test.00013.wav', 'Test\\test.00014.wav', 'Test\\test.00015.wav', 'Test\\test.00016.wav', 'Test\\test.00017.wav', 'Test\\test.00018.wav', 'Test\\test.00019.wav', 'Test\\test.00020.wav', 'Test\\test.00021.wav', 'Test\\test.00022.wav', 'Test\\test.00023.wav', 'Test\\test.00024.wav', 'Test\\test.00025.wav', 'Test\\test.00026.wav', 'Test\\test.00027.wav', 'Test\\test.00028.wav', 'Test\\test.00029.wav', 'Test\\test.00030.wav', 'Test\\test.00031.wav', 'Test\\test.00032.wav', 'Test\\test.00033.wav', 'Test\\test.00034.wav', 'Test\\test.00035.wav', 'Test\\test.00036.wav', 'Test\\test.00037.wav', 'Test\\test.00038.wav', 'Test\\test.00039.wav', 'Test\\test.00040.wav', 'Test\\test.000

### Audio eigenschappen

Vermeld de eigenschappen van het audiobestand, zoals de duur en de
samplingsfrequentie.

In [23]:
import pandas as pd

audio_features = []

for af in audio_files:
    y, sr = librosa.load(af, sr=None)
    duration = len(y) / sr
    
    # Voorbeeld: tempo
    tempo, _ = librosa.beat.beat_track(y=y, sr=sr)
    
    # Voorbeeld: gemiddelde zero crossing rate
    zcr = librosa.feature.zero_crossing_rate(y)
    mean_zcr = zcr.mean()
    
    # Voeg toe aan lijst
    audio_features.append({
        'filename': os.path.basename(af),
        'duration': duration,
        'sampling_rate': sr,
        'tempo': tempo,
        'mean_zcr': mean_zcr
    })

df_audio = pd.DataFrame(audio_features)
df_audio.head()

import pandas as pd

audio_features = []

for af in audio_files:
    y, sr = librosa.load(af, sr=None)
    duration = len(y) / sr
    
    # Voorbeeld: tempo
    tempo, _ = librosa.beat.beat_track(y=y, sr=sr)
    
    # Voorbeeld: gemiddelde zero crossing rate
    zcr = librosa.feature.zero_crossing_rate(y)
    mean_zcr = zcr.mean()
    
    # Voeg toe aan lijst
    audio_features.append({
        'filename': os.path.basename(af),
        'duration': duration,
        'sampling_rate': sr,
        'tempo': tempo,
        'mean_zcr': mean_zcr
    })

df_audio = pd.DataFrame(audio_features)
df_audio.head()

filename   duration  sampling_rate                 tempo  mean_zcr
0  test.00000.wav  30.013333          22050  [112.34714673913044]  0.122906
1  test.00001.wav  30.013333          22050         [143.5546875]  0.059545
2  test.00002.wav  30.000181          22050          [103.359375]  0.177561
3  test.00003.wav  30.000181          22050  [112.34714673913044]  0.088859
4  test.00004.wav  30.121542          22050  [117.45383522727273]  0.096525

### Inlezen songteksten

Laad de songteksten en analyseer ze. Controleer bijvoorbeeld de lengte van de teksten per genre en op veel voorkomende woorden.

### Relatie bestanden

Onderzoek de relaties tussen audiokenmerken, songteksten en de target-genres.

### EDA Conclusie

Beschrijf wat de belangrijkste bevindingen zijn van de EDA.

## LSTM voor audioclips

### Modelbouwing 

In deze deelopdracht werk je uitsluitend met de audioclips en niet met de lyrics.

Bouw en train een LSTM-model om de genres te voorspellen op basis van de
audiodata.

### Uitleg model

Plot je modelarchitectuur met behulp van een geschikte visualisatietool.

### Feature Engineering

Beschrijf in detail welke stappen je onderneemt voor feature engineering.

### Model onderbouwing

Onderbouw je keuzes van het aantal LSTM-lagen, het aantal dense lagen, het aantal
LSTM-units en neuronen per laag, de activeringsfuncties, de keuze van de optimizer
en het aantal trainingsepochs.

### Model compileren

Beschrijf welke lossfunctie het meest geschikt is voor dit probleem. Kies een
geschikte optimizer en beschrijf kort hoe deze optimizer werkt. Compile je model
met de gekozen lossfunctie en optimizer, en train deze op de audiogegevens.

##  LSTM voor songteksten

### Modelbouwing 
In deze deelopdracht werk je alleen met de lyrics en labels, en niet met de audiodata.


Bouw en train een LSTM-model om de genres te voorspellen op basis van de lyrics.

### Uitleg model

Plot je modelarchitectuur met behulp van een geschikte visualisatietool.

### Model onderbouwing

Onderbouw je keuzes van het aantal LSTM-lagen, het aantal dense lagen, het aantal
LSTM-units en neuronen per laag, de activeringsfuncties, de keuze van de optimizer
en het aantal trainingsepochs.

### Feature Engineering

Beschrijf welke vormen van data preprocessing, feature engineering, of/en data augmentation (indien van toepassing ) geschikt zijn voor dit probleem. Implementeer dit in je datapijplijn.

### Model compileren

Compile je model met je gekozen lossfunctie en optimizer, en train deze op de tekstdata.

## Transformer voor songteksten 

### Modelbouwing 
In deze deelopdracht werk je alleen met de lyrics en labels, en niet met de audiodata. 

Bouw en train een transformer-model om de genres te voorspellen op basis van de lyrics.

Voor deze opdracht kies je een voorgetraind model van Hugging Face en fine-tune dit op de songtekstdataset.

Geef de naam op van de modelarchitectuur die je hebt gekozen en de dataset waarop deze vooraf is getraind.

### Uitleg model

Noem de voordelen van het gebruik van vooraf getrainde tekstmodellen en leg ze uit.

### Model fine tuning

Beschrijf in detail de stappen die worden genomen bij het finetunen van een vooraf getraind transformermodel.

### Model verbeteren

Je bent vrij om hier aanvullende technieken voor regularisatie, data augmentation, finetuning van hyperparameters, enz. te gebruiken om je classificatiescore te verbeteren. Motiveer je keuzes.

### Model compileren

Compile je model met je gekozen lossfunctie en optimizer. (Staat niet direct in de opdracht)

## Model naar keuze

Dit is een vrije keuze deelopdracht. Je bent vrij om de tekst, de audio of beide te gebruiken. Bouw en train een model, of een ensemble van modellen, dat de best mogelijke accuracy op deze dataset geeft.

### Uitleg Model

Plot je modelarchitectuur / architecturen met behulp van een geschikte visualisatietool.

### Model beschrijving

Beschrijf in detail de keuzes die je hebt gemaakt bij het maken en trainen van dit model(len). Motiveer je keuzes.

## Bevindingen

Geef een samenvatting van de uitkomsten van het modelleren.
- Geef een beknopt overzicht van de resultaten. 
- Welke model presteert het beste? Bij welke parameters?
- Toon je scores op Kaggle en laat zien wat de resultaten waren van je verbeteringen op je score op Kaggle.


## Conclusie en aanbevelingen 

## Modelleringsproces en uitdagingen

Beschrijf het modelleringsproces voor deze opdracht. Wat waren de uitdagingen daarmee?

### Modellen - Wat werkte het beste?

In deze opdracht heb je verschillende modelarchitecturen uitgeprobeerd, en verschillende technieken om de prestaties te verbeteren. Welke van deze werkte het beste? Welke van deze werkte niet goed? Waarom denk je dat dat het geval was?

### Modellen - Welke werkte het beste?

Welke modellen gaven de beste resultaten wat betreft de audiofragmenten? Welke modellen presteerden het beste met de tekstinput?

### Genres - Welke goed te voorspellen?

- Welke genres waren gemakkelijker te voorspellen met behulp van songteksten? 
- Welke genres waren gemakkelijker te voorspellen met behulp van audio?

### Aanbevelingen
Als een bedrijf zou besluiten om op basis van jouw werk in deze opdracht een geautomatiseerde app voor audioclassificatie te maken, wat zou dan jouw advies zijn?

### Uitbreidings mogelijkheden
Hoe zou je, conceptueel gezien, het werk dat in deze opdracht is gedaan, uitbreiden om een systeem voor muziekaanbevelingen te creëren?

[//]: # (Lars stinkt)

conclusie blah blah